In [1]:
!trtexec

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec
=== Model Options ===
  --uff=<file>                UFF model
  --onnx=<file>               ONNX model
  --model=<file>              Caffe model (default = no model, random weights used)
  --deploy=<file>             Caffe prototxt file
  --output=<name>[,<name>]*   Output names (it can be specified multiple times); at least one output is required for UFF and Caffe
  --uffInput=<name>,X,Y,Z     Input blob name and its dimensions (X,Y,Z=C,H,W), it can be specified multiple times; at least one is required for UFF models
  --uffNHWC                   Set if inputs are in the NHWC layout instead of NCHW (use X,Y,Z=H,W,C order in --uffInput)

=== Build Options ===
  --maxBatch                  Set max batch size and build an implicit batch engine (default = same size as --batch)
                              This option should not be used when the input model is ONNX or when dynamic shapes are provided.
  --minShapes=spec            B

In [2]:
import os

In [3]:
ONNX_MODEL_DIR = './Flask/Models/'

FLASK_MODEL_DIR = './Flask/Models/'

TRITON_MODEL_DIR = './Triton/Models/'
TRITON_CONFIG_FILE = 'config.pbtxt'
TRITON_MODEL_FILE = 'model.plan'

In [4]:
def save_tensorrt_model(onnx_model, trt_model, precision, config):
    trt_model = trt_model + '_' + precision
    onnx_model_path = os.path.join(ONNX_MODEL_DIR, onnx_model + '.onnx')
    flask_model_path = os.path.join(FLASK_MODEL_DIR, trt_model + '.plan')

    !trtexec \
        --onnx=$onnx_model_path \
        --explicitBatch \
        --$precision \
        --saveEngine=$flask_model_path

    triton_config_path = os.path.join(TRITON_MODEL_DIR, trt_model, TRITON_CONFIG_FILE)
    os.makedirs(os.path.dirname(triton_config_path), exist_ok=True)
    with open(triton_config_path, 'w') as f:
        f.write(config.strip())

    triton_model_path = os.path.join(TRITON_MODEL_DIR, trt_model, '1', TRITON_MODEL_FILE)
    os.makedirs(os.path.dirname(triton_model_path), exist_ok=True)
    !cp $flask_model_path $triton_model_path
        
    print(flask_model_path)
    print(triton_config_path)
    print(triton_model_path)
    return

In [5]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/resnet34-trt_best.plan
[09/16/2022-08:41:30] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:41:30] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:41:30] [I] === Model Options ===
[09/16/2022-08:41:30] [I] Format: ONNX
[09/16/2022-08:41:30] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-08:41:30] [I] Output:
[09/16/2022-08:41:30] [I] === Build Options ===
[09/16/2022-08:41:30] [I] Max batch: explicit batch
[09/16/2022-08:41:30] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:41:30] [I] minTiming: 1
[09/16/2022-08:41:30] [I] avgTiming: 8
[09/16/2022-08:41:30] [I] Precision: FP32+FP16+INT8
[09/16/2022-08:41:30] [I] LayerPrecisions: 
[09

[09/16/2022-08:41:39] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:39] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:41:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:39] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:39] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:41:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the wei

[09/16/2022-08:41:41] [W] [TRT] Weights [name=Conv_10 + Add_11 + Relu_12.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:41] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:41] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:41] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-08:41:43] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:43] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:43] [W] [TRT] Weights [name=Conv_20 + Add_22 + Relu_23.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with r

[09/16/2022-08:41:46] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:46] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:46] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:46] [W] [TRT] If this is not the desired behavior, pleas

...

[09/16/2022-08:41:58] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:58] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:58] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:58] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:58] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:58] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:41:58] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-08:41:58] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:41:58] [W] [TRT] If this is not the desired behavior, pleas

[09/16/2022-08:42:02] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:02] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:02] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:02] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce th

[09/16/2022-08:42:03] [W] [TRT] Weights [name=Conv_83 + Add_84 + Relu_85.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:03] [W] [TRT] Weights [name=Conv_83 + Add_84 + Relu_85.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:04] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:04] [W] [TRT] If this is not the desired behavior, please modify the weight

[09/16/2022-08:42:05] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:05] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/16/2022-08:42:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:05] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

./Flask/Models/resnet34-trt_best.plan
./Triton/Models/resnet34-trt_best/config.pbtxt
./Triton/Models/resnet34-trt_best/1/model.plan


In [6]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/resnet34-trt_fp16.plan
[09/16/2022-08:42:09] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:42:09] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:42:09] [I] === Model Options ===
[09/16/2022-08:42:09] [I] Format: ONNX
[09/16/2022-08:42:09] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-08:42:09] [I] Output:
[09/16/2022-08:42:09] [I] === Build Options ===
[09/16/2022-08:42:09] [I] Max batch: explicit batch
[09/16/2022-08:42:09] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:42:09] [I] minTiming: 1
[09/16/2022-08:42:09] [I] avgTiming: 8
[09/16/2022-08:42:09] [I] Precision: FP32+FP16
[09/16/2022-08:42:09] [I] LayerPrecisions: 
[09/16/2

[09/16/2022-08:42:14] [W] [TRT] Weights [name=Conv_0 + Relu_1.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:14] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:14] [W] [TRT] Weights [name=Conv_0 + Relu_1.bias] had the following issues when converted to FP16:
[09/16/2022-08:42:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:14] [W] [TRT] Weights [name=Conv_0 + Relu_1.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:14] [W] [

[09/16/2022-08:42:15] [W] [TRT] Weights [name=Conv_5 + Add_6 + Relu_7.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:15] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:15] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:16] [W] [TRT] Weights [name=Conv_8 + Relu_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:16] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:16] [W] [TRT] Weights [name=Conv_8 + Relu_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:42

[09/16/2022-08:42:16] [W] [TRT] Weights [name=Conv_18 + Relu_19.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:16] [W] [TRT] Weights [name=Conv_18 + Relu_19.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:16] [W] [TRT] Weights [name=Conv_18 + Relu_19.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:16] [W] [TRT] If this is not the desired behavior, please modify the weights or ret

[09/16/2022-08:42:18] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:18] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:18] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:18] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

...

[09/16/2022-08:42:28] [W] [TRT] Weights [name=Conv_76 + Relu_77.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:28] [W] [TRT] Weights [name=Conv_76 + Relu_77.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

[09/16/2022-08:42:30] [W] [TRT] Weights [name=Conv_81 + Relu_82.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:30] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:30] [W] [TRT] Weights [name=Conv_83 + Add_84 + Relu_85.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:30] [W] [TRT] Weights [name=Conv_83 + Add_84 + Relu_85.weight] had the following issues when converted to FP16:
[

[09/16/2022-08:42:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:31] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/16/2022-08:42:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:31] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-08:42:31] [W] [TRT] Weights [name=Conv_70 + Relu_71.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:31] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:42:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:31] [W] [TRT] Weights [name=Conv_73.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:42:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:42:31] [W] [TRT] Weights [name=Conv_72 + Add_74 + Relu_75.weight] had the following issues when converted to FP16:
[09/16/2022-08:42:31

./Flask/Models/resnet34-trt_fp16.plan
./Triton/Models/resnet34-trt_fp16/config.pbtxt
./Triton/Models/resnet34-trt_fp16/1/model.plan


In [7]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/resnet34-trt_int8.plan
[09/16/2022-08:42:35] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:42:35] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:42:35] [I] === Model Options ===
[09/16/2022-08:42:35] [I] Format: ONNX
[09/16/2022-08:42:35] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/16/2022-08:42:35] [I] Output:
[09/16/2022-08:42:35] [I] === Build Options ===
[09/16/2022-08:42:35] [I] Max batch: explicit batch
[09/16/2022-08:42:35] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:42:35] [I] minTiming: 1
[09/16/2022-08:42:35] [I] avgTiming: 8
[09/16/2022-08:42:35] [I] Precision: FP32+INT8
[09/16/2022-08:42:35] [I] LayerPrecisions: 
[09/16/2

./Flask/Models/resnet34-trt_int8.plan
./Triton/Models/resnet34-trt_int8/config.pbtxt
./Triton/Models/resnet34-trt_int8/1/model.plan


In [8]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/mobilenet_v2-trt_best.plan
[09/16/2022-08:42:57] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:42:57] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:42:57] [I] === Model Options ===
[09/16/2022-08:42:57] [I] Format: ONNX
[09/16/2022-08:42:57] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-08:42:57] [I] Output:
[09/16/2022-08:42:57] [I] === Build Options ===
[09/16/2022-08:42:57] [I] Max batch: explicit batch
[09/16/2022-08:42:57] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:42:57] [I] minTiming: 1
[09/16/2022-08:42:57] [I] avgTiming: 8
[09/16/2022-08:42:57] [I] Precision: FP32+FP16+INT8
[09/16/2022-08:42:57] [I] LayerPrec

[09/16/2022-08:43:18] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:18] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:22] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:22] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-08:43:26] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:26] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:26] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/16/2022-08:43:31] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:31] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:31] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:31] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:43:31] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:31] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-08:43:34] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:34] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:34] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:34] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:43:34] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-08:43:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:43:34] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

...

[09/16/2022-08:44:13] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:13] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:13] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:13] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:13] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:13] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:13] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:13] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:13] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-08:44:14] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:14] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:14] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:14] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-08:44:17] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:17] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:44:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:17] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/16/2022-08:44:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:17] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:17] [W] [TRT]  - Subnormal FP16 v

[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199585 ms - Host latency: 0.230005 ms (enqueue 0.145483 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199976 ms - Host latency: 0.230933 ms (enqueue 0.145459 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199243 ms - Host latency: 0.229687 ms (enqueue 0.146143 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199146 ms - Host latency: 0.229761 ms (enqueue 0.146997 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199268 ms - Host latency: 0.22981 ms (enqueue 0.146143 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199146 ms - Host latency: 0.230054 ms (enqueue 0.146094 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199219 ms - Host latency: 0.229932 ms (enqueue 0.14585 ms)
[09/16/2022-08:44:21] [I] Average on 10 runs - GPU latency: 0.199097 ms - Host latency: 0.229712 ms (enqueue 0.146704 ms)
[09/16/2022-08:44:21] [I] 

./Flask/Models/mobilenet_v2-trt_best.plan
./Triton/Models/mobilenet_v2-trt_best/config.pbtxt
./Triton/Models/mobilenet_v2-trt_best/1/model.plan


In [9]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/mobilenet_v2-trt_fp16.plan
[09/16/2022-08:44:21] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:44:21] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:44:21] [I] === Model Options ===
[09/16/2022-08:44:21] [I] Format: ONNX
[09/16/2022-08:44:21] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-08:44:21] [I] Output:
[09/16/2022-08:44:21] [I] === Build Options ===
[09/16/2022-08:44:21] [I] Max batch: explicit batch
[09/16/2022-08:44:21] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:44:21] [I] minTiming: 1
[09/16/2022-08:44:21] [I] avgTiming: 8
[09/16/2022-08:44:21] [I] Precision: FP32+FP16
[09/16/2022-08:44:21] [I] LayerPrecision

[09/16/2022-08:44:30] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:34] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:34] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:34] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:34] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/16/2022-08:44:37] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:37] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:37] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:37] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:37] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:37] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:37] [W] [TRT] Weights [name=Conv_10 + PWN(Clip_11).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:37] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:37] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regular

[09/16/2022-08:44:40] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:40] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:40] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:40] [W] [TRT] If this is not the desired behavior, please modify the

[09/16/2022-08:44:43] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:43] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/16/2022-08:44:43] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:43] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:44:44] [W] [TRT] Weights [name=Conv_21 + PWN(Clip_22).weight] had the following issues when converted to FP16:
[09/16/2022-08:44:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:44:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regul

...

[09/16/2022-08:45:16] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:16] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:16] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-08:45:17] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:45:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:17] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:45:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:18] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:18] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. 

[09/16/2022-08:45:18] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:18] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:45:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:18] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/16/2022-08:45:18] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:18] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:18] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:18] [W] [TRT]  - Subnormal FP16 v

[09/16/2022-08:45:19] [W] [TRT] Weights [name=Conv_90 + PWN(Clip_91).weight] had the following issues when converted to FP16:
[09/16/2022-08:45:19] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:19] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:45:19] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:19] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/16/2022-08:45:19] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:45:19] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:45:19] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/16/2022-08:45:1

./Flask/Models/mobilenet_v2-trt_fp16.plan
./Triton/Models/mobilenet_v2-trt_fp16/config.pbtxt
./Triton/Models/mobilenet_v2-trt_fp16/1/model.plan


In [10]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/mobilenet_v2-trt_int8.plan
[09/16/2022-08:45:23] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:45:23] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:45:23] [I] === Model Options ===
[09/16/2022-08:45:23] [I] Format: ONNX
[09/16/2022-08:45:23] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/16/2022-08:45:23] [I] Output:
[09/16/2022-08:45:23] [I] === Build Options ===
[09/16/2022-08:45:23] [I] Max batch: explicit batch
[09/16/2022-08:45:23] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:45:23] [I] minTiming: 1
[09/16/2022-08:45:23] [I] avgTiming: 8
[09/16/2022-08:45:23] [I] Precision: FP32+INT8
[09/16/2022-08:45:23] [I] LayerPrecision

./Flask/Models/mobilenet_v2-trt_int8.plan
./Triton/Models/mobilenet_v2-trt_int8/config.pbtxt
./Triton/Models/mobilenet_v2-trt_int8/1/model.plan


In [11]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b0-trt_best.plan
[09/16/2022-08:46:13] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:46:13] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:46:13] [I] === Model Options ===
[09/16/2022-08:46:13] [I] Format: ONNX
[09/16/2022-08:46:13] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-08:46:13] [I] Output:
[09/16/2022-08:46:13] [I] === Build Options ===
[09/16/2022-08:46:13] [I] Max batch: explicit batch
[09/16/2022-08:46:13] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:46:13] [I] minTiming: 1
[09/16/2022-08:46:13] [I] avgTiming: 8
[09/16/2022-08:46:13] [I] Precision: FP32+FP16+INT8
[09/16/2022-08:46:13] [I] 

[09/16/2022-08:48:10] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:10] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:10] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:10] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:10] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-08:48:11] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:11] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:11] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:11] [W] [TRT] If thi

[09/16/2022-08:48:22] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:22] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:22] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrai

[09/16/2022-08:48:23] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:23] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:23] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:23] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:23] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:23] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:23] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:23] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:23] [W] [TRT] If thi

...

[09/16/2022-08:48:46] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:46] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:46] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:46] [W] [TRT] Weights [name=Conv_222 + PWN(PWN(Sigmoid_223), Mul_224).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:46] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:46] [W] [TR

[09/16/2022-08:48:47] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:47] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:47] [W] [TRT] Weights [name=Conv_232.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to

[09/16/2022-08:48:48] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:48] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:48] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:48] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:48] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-08:48:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:48] [W] [TR

[09/16/2022-08:48:49] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:49] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/16/2022-08:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:48:49] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-08:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

./Flask/Models/efficientnet_b0-trt_best.plan
./Triton/Models/efficientnet_b0-trt_best/config.pbtxt
./Triton/Models/efficientnet_b0-trt_best/1/model.plan


In [12]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b0-trt_fp16.plan
[09/16/2022-08:48:54] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:48:54] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:48:54] [I] === Model Options ===
[09/16/2022-08:48:54] [I] Format: ONNX
[09/16/2022-08:48:54] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-08:48:54] [I] Output:
[09/16/2022-08:48:54] [I] === Build Options ===
[09/16/2022-08:48:54] [I] Max batch: explicit batch
[09/16/2022-08:48:54] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:48:54] [I] minTiming: 1
[09/16/2022-08:48:54] [I] avgTiming: 8
[09/16/2022-08:48:54] [I] Precision: FP32+FP16
[09/16/2022-08:48:54] [I] Layer

[09/16/2022-08:50:47] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-08:50:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:50:47] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:50:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:50:47] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-08:50:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:50:47] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:50:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with reg

[09/16/2022-08:50:55] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/16/2022-08:50:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:50:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:50:55] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/16/2022-08:50:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:50:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:51:00] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/16/2022-08:51:00] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:00] [W] [TRT] If thi

[09/16/2022-08:51:03] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-08:51:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:51:03] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/16/2022-08:51:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:51:04] [W] [TRT] Weights [name=Conv_43 + PWN(PWN(Sigmoid_44), Mul_45).weight] had the following issues when converted to FP16:
[09/16/2022-08:51:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:04] [W] [TRT] If this is not the desired behavior, please modify

[09/16/2022-08:51:06] [W] [TRT] Weights [name=Conv_53.weight] had the following issues when converted to FP16:
[09/16/2022-08:51:06] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:06] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:51:06] [W] [TRT] Weights [name=Conv_53.weight] had the following issues when converted to FP16:
[09/16/2022-08:51:06] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:06] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:51:06] [W] [TRT] Weights [name=Conv_53.weight] had the following issues when converted to FP16:
[09/16/2022-08:51:06] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:51:06] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

...

[09/16/2022-08:52:16] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-08:52:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:16] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/16/2022-08:52:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:16] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:16] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-08:52:16] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:16] [W] [TRT] If this is not the desired beh

[09/16/2022-08:52:17] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-08:52:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:17] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/16/2022-08:52:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:17] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/16/2022-08:52:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

[09/16/2022-08:52:17] [W] [TRT] Weights [name=Conv_184.weight] had the following issues when converted to FP16:
[09/16/2022-08:52:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:17] [W] [TRT] Weights [name=Conv_187 + Add_188.weight] had the following issues when converted to FP16:
[09/16/2022-08:52:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:52:17] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:52:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:52:17] [W] [TRT] Weights [name=Conv_189 + PWN(PWN(Sigmoid_190), Mul_191).weight] had the following issues when converted to FP16:
[09

[09/16/2022-08:52:17] [I] Engine built in 203.901 sec.
[09/16/2022-08:52:17] [I] [TRT] [MemUsageChange] Init CUDA: CPU +0, GPU +0, now: CPU 1377, GPU 705 (MiB)
[09/16/2022-08:52:17] [I] [TRT] Loaded engine size: 13 MiB
[09/16/2022-08:52:17] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in engine deserialization: CPU +0, GPU +12, now: CPU 0, GPU 12 (MiB)
[09/16/2022-08:52:17] [I] Engine deserialized in 0.0208959 sec.
[09/16/2022-08:52:17] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in IExecutionContext creation: CPU +0, GPU +4, now: CPU 0, GPU 16 (MiB)
[09/16/2022-08:52:17] [I] Using random values for input input_0
[09/16/2022-08:52:17] [I] Created input binding for input_0 with dimensions 1x3x224x224
[09/16/2022-08:52:17] [I] Using random values for output output_0
[09/16/2022-08:52:17] [I] Created output binding for output_0 with dimensions 1x1000
[09/16/2022-08:52:17] [I] Starting inference
[09/16/2022-08:52:21] [I] Warmup completed 320 queries over 200 ms
[09/16/

./Flask/Models/efficientnet_b0-trt_fp16.plan
./Triton/Models/efficientnet_b0-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b0-trt_fp16/1/model.plan


In [13]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b0-trt_int8.plan
[09/16/2022-08:52:21] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:52:21] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:52:21] [I] === Model Options ===
[09/16/2022-08:52:21] [I] Format: ONNX
[09/16/2022-08:52:21] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/16/2022-08:52:21] [I] Output:
[09/16/2022-08:52:21] [I] === Build Options ===
[09/16/2022-08:52:21] [I] Max batch: explicit batch
[09/16/2022-08:52:21] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:52:21] [I] minTiming: 1
[09/16/2022-08:52:21] [I] avgTiming: 8
[09/16/2022-08:52:21] [I] Precision: FP32+INT8
[09/16/2022-08:52:21] [I] Layer

./Flask/Models/efficientnet_b0-trt_int8.plan
./Triton/Models/efficientnet_b0-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b0-trt_int8/1/model.plan


In [14]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b7-trt_best.plan
[09/16/2022-08:53:42] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:53:42] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:53:42] [I] === Model Options ===
[09/16/2022-08:53:42] [I] Format: ONNX
[09/16/2022-08:53:42] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-08:53:42] [I] Output:
[09/16/2022-08:53:42] [I] === Build Options ===
[09/16/2022-08:53:42] [I] Max batch: explicit batch
[09/16/2022-08:53:42] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:53:42] [I] minTiming: 1
[09/16/2022-08:53:42] [I] avgTiming: 8
[09/16/2022-08:53:42] [I] Precision: FP32+FP16+INT8
[09/16/2022-08:53:42] [I] 

[09/16/2022-08:55:20] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-08:55:20] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:20] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:20] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-08:55:20] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:20] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:20] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/16/2022-08:55:20] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:20] [W] [TRT] If this is not 

[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:55:22] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:55:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:55:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-08:56:25] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-08:56:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:56:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:56:25] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-08:56:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:56:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:56:25] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/16/2022-08:56:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:56:25] [W] [TRT] If thi

...

[09/16/2022-08:57:33] [W] [TRT] Weights [name=Conv_804.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:33] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:57:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:57:33] [W] [TRT] Weights [name=Conv_804.bias] had the following issues when converted to FP16:
[09/16/2022-08:57:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:57:33] [W] [TRT] Weights [name=Conv_804.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:33] [W] [TRT]  - Subnormal FP1

[09/16/2022-08:57:33] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:33] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:57:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:57:33] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:33] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:57:33] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of t

[09/16/2022-08:57:34] [W] [TRT] Weights [name=Gemm_814.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:34] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:34] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:57:34] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:57:35] [W] [TRT] Weights [name=Gemm_814.weight] had the following issues when converted to FP16:
[09/16/2022-08:57:35] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:57:35] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-08:57:35] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2

[09/16/2022-08:57:37] [I] [TRT] Total Host Persistent Memory: 510016
[09/16/2022-08:57:37] [I] [TRT] Total Device Persistent Memory: 0
[09/16/2022-08:57:37] [I] [TRT] Total Scratch Memory: 22536
[09/16/2022-08:57:37] [I] [TRT] [MemUsageStats] Peak memory usage of TRT CPU/GPU memory allocators: CPU 66 MiB, GPU 20460 MiB
[09/16/2022-08:57:37] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 117.077ms to assign 5 blocks to 392 nodes requiring 28081152 bytes.
[09/16/2022-08:57:37] [I] [TRT] Total Activation Memory: 28081152
[09/16/2022-08:57:37] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in building engine: CPU +64, GPU +66, now: CPU 64, GPU 66 (MiB)
[09/16/2022-08:57:37] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/16/2022-08:57:37] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built fr

./Flask/Models/efficientnet_b7-trt_best.plan
./Triton/Models/efficientnet_b7-trt_best/config.pbtxt
./Triton/Models/efficientnet_b7-trt_best/1/model.plan


In [15]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b7-trt_fp16.plan
[09/16/2022-08:57:41] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-08:57:41] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-08:57:41] [I] === Model Options ===
[09/16/2022-08:57:41] [I] Format: ONNX
[09/16/2022-08:57:41] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-08:57:41] [I] Output:
[09/16/2022-08:57:41] [I] === Build Options ===
[09/16/2022-08:57:41] [I] Max batch: explicit batch
[09/16/2022-08:57:41] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-08:57:41] [I] minTiming: 1
[09/16/2022-08:57:41] [I] avgTiming: 8
[09/16/2022-08:57:41] [I] Precision: FP32+FP16
[09/16/2022-08:57:41] [I] Layer

[09/16/2022-08:58:11] [W] [TRT] Weights [name=Conv_0.weight] had the following issues when converted to FP16:
[09/16/2022-08:58:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:58:49] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/16/2022-08:58:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:58:51] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/16/2022-08:58:51] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:51] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/16/2022-08:58:59] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:58:59] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:59] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:58:59] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/16/2022-08:58:59] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:59] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:58:59] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/16/2022-08:58:59] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:58:59] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/16/2022-08:59:41] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-08:59:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:59:41] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-08:59:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:59:41] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/16/2022-08:59:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-08:59:47] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-08:59:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:59:47] [W] [TRT] Weights [name=Conv_21.bias] had the following issues when converted to FP16:
[09/16/2022-08:59:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-08:59:47] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/16/2022-08:59:47] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-08:59:47] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

...

[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_658 + Add_659.weight] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_660 + PWN(PWN(Sigmoid_661), Mul_662).weight] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_703 + Add_704.weight] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_703 + Add_704.bias] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_705 + PWN(PWN(Sigmoid_706), Mul_707).weight] had the following issues when converted to F

[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_742 + PWN(PWN(Sigmoid_743), Mul_744).weight] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_742 + PWN(PWN(Sigmoid_743), Mul_744).bias] had the following issues when converted to FP16:
[09/16/2022-09:02:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:57] [W] [TRT] Weights [name=Conv_745.weight] had the following issues when c

[09/16/2022-09:02:58] [W] [TRT] Weights [name=Conv_794 + PWN(PWN(Sigmoid_795), Mul_796).weight] had the following issues when converted to FP16:
[09/16/2022-09:02:58] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:58] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/16/2022-09:02:58] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:58] [W] [TRT] Weights [name=Conv_794 + PWN(PWN(Sigmoid_795), Mul_796).bias] had the following issues when converted to FP16:
[09/16/2022-09:02:58] [W] [TRT]  - Subnormal FP16 values detected. 
[09/16/2022-09:02:58] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/16/2022-09:02:58] [W] [TRT] Weights [name=Conv_797.weight] had the following issues when c

./Flask/Models/efficientnet_b7-trt_fp16.plan
./Triton/Models/efficientnet_b7-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b7-trt_fp16/1/model.plan


In [16]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input_0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output_0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b7-trt_int8.plan
[09/16/2022-09:03:03] [W] --explicitBatch flag has been deprecated and has no effect!
[09/16/2022-09:03:03] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/16/2022-09:03:03] [I] === Model Options ===
[09/16/2022-09:03:03] [I] Format: ONNX
[09/16/2022-09:03:03] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/16/2022-09:03:03] [I] Output:
[09/16/2022-09:03:03] [I] === Build Options ===
[09/16/2022-09:03:03] [I] Max batch: explicit batch
[09/16/2022-09:03:03] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/16/2022-09:03:03] [I] minTiming: 1
[09/16/2022-09:03:03] [I] avgTiming: 8
[09/16/2022-09:03:03] [I] Precision: FP32+INT8
[09/16/2022-09:03:03] [I] Layer

./Flask/Models/efficientnet_b7-trt_int8.plan
./Triton/Models/efficientnet_b7-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b7-trt_int8/1/model.plan
